In [359]:
pip install plotly

In [24]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

#Libs para importar os modelos que serão utilizados e para verificar a precisão dos mesmo
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support as score
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn import tree

#Lib criada pela equipe para fazer os devidos tratamentos dos tweets.
from remove_normalizer import ajustandoDados

#lib de plotagem
import plotly.graph_objects as go

#Lib para salvarmos os modelos, CountVectorizer e as categorias alvos para utilizarmos posteriormente sem a necessidade de treinarmos o modelo novamente
import joblib

Lemos o aqruivo excel e transformamos em um dataframe

In [3]:
tweets = pd.read_excel('C:/Users/rafae/OneDrive/Documents/GitHub/Tweet_Classifier/Final/dados/train_data/dados_unidos_oficial_semDuplicatas.xlsx')
print(tweets.head())

                                           full_text classificacao_texto  \
0    acho q o bozo errou o time chegou meio atrasado              neutro   
1                                  jair em desespero            negativo   
2                                    armacao do jair            negativo   
3   camilamoreno13_ jonvlogs raciocinio bom e o t...            negativo   
4  campanha de bolsonaro acusacao sem provas reai...            negativo   

   classificacao  
0              0  
1             -1  
2             -1  
3             -1  
4             -1  


Retirando colunas que não serão utilizadas pelo modelo

Selecionamos os resultados que o modelo que iremos utilizar deverá dar.

In [4]:
categoria_alvo = tweets['classificacao_texto'].unique()
print(categoria_alvo)

['neutro' 'negativo' 'positivo']


#### Verificando a quantidade de dados por classificação

Aqui estamos fazendo um groupby da coluna "classificacao_texto", onde fala se o tweet é positivo, negativo ou neutro. Com isso

In [5]:
classificacao = tweets.groupby('classificacao_texto').classificacao.value_counts()
classificacao = pd.DataFrame(classificacao)
classificacao.reset_index(names=['classificacao_texto','classificacao1'],inplace=True)
classificacao.rename(columns = {'classificacao1':'classificacao', 'classificacao':'soma'}, inplace = True)
display(classificacao.head())
print(f'Total de Classificação de Lula: {classificacao.soma.sum()}')

classificacao_texto  classificacao  soma
0            negativo             -1   200
1              neutro              0    79
2            positivo              1   134

Total de Classificação de Lula: 413


Aqui verificamos que dentre 405 tweets as classificações ficam distribuidas da seguinte maneira, 49% classificações negativas, 18% neutras e 33% positivas.

In [6]:
fig = go.Figure(data=[
    go.Bar(name='Total', x=classificacao['classificacao_texto'], y=classificacao["soma"], text=classificacao["soma"])
])
# Change the bar mode
fig.update_layout(title = "Quantidade de Classificação")
fig.show()

Aqui criamos uma máscara para selecionar os tweets apenas para um candidato.

Essas máscaras foram criadas para verificarmos como estão distribuidas as classificações por candidato.

In [7]:
#Dataframe que aparece palavras referentes ao Lula
searchLula = ['lula' , 'lulalivre' , 'lulaladrao' , 'molusco' , 'lulaladrão' , 'lulapresidente','lula13']
mask_lula = tweets['full_text'].str.contains('|'.join(searchLula))
lula_df = tweets[mask_lula]
#Dataframe que aparece palavras referentes ao bolsonaro
searchBolsonaro = ['bolsonaro', 'bozo', 'bozonaro', 'elenão', 'elesim', 'jair', 'mito',' bolsonaro22']
mask_bolso = tweets['full_text'].str.contains('|'.join(searchBolsonaro))
bolsonaro_df = tweets[mask_bolso]

Aqui geramos o dataframe apenas com os tweets que mencionam o Lula.

In [8]:
classificacao_lula = lula_df.groupby('classificacao_texto').classificacao.value_counts()
classificacao_lula = pd.DataFrame(classificacao_lula)
classificacao_lula.reset_index(names=['classificacao_texto','classificacao1'],inplace=True)
classificacao_lula.rename(columns = {'classificacao1':'classificacao', 'classificacao':'soma'}, inplace = True)
display(classificacao_lula.head())
print(f'Total de Classificação de Lula: {classificacao_lula.soma.sum()}')

classificacao_texto  classificacao  soma
0            negativo             -1   102
1              neutro              0    25
2            positivo              1   109

Total de Classificação de Lula: 236


Aqui geramos o dataframe apenas com os tweets que mencionam o Bolsonaro.

In [9]:
classificacao_bolsonaro = bolsonaro_df.groupby('classificacao_texto').classificacao.value_counts()
classificacao_bolsonaro = pd.DataFrame(classificacao_bolsonaro)
classificacao_bolsonaro.reset_index(names=['classificacao_texto','classificacao1'],inplace=True)
classificacao_bolsonaro.rename(columns = {'classificacao1':'classificacao', 'classificacao':'soma'}, inplace = True)
display(classificacao_bolsonaro.head())
print(f'Total de Classificação de Bolsonaro: {classificacao_bolsonaro.soma.sum()}')

classificacao_texto  classificacao  soma
0            negativo             -1   125
1              neutro              0    28
2            positivo              1    60

Total de Classificação de Bolsonaro: 213


Quando olhamos para classificação por presidente veficamos que Lula que possuí 228 tweets que é mencionado e a classificação desses tweets são distribuidas da seguinte maneira, como mostrada na fig. X, 44% são classificações negativas, 8% são neutras e 47% são possitivas. Quando olhamos para a distribuição de Bolsonaro, onde seu nome é mencionado em 210 tweets percebemos que a distribuição é dada da seguinte maneira: 59% são negativas, 12% são neutras e 28% são positivas.

In [10]:
fig = go.Figure(data=[
    go.Bar(name='Lula', x=classificacao_lula['classificacao_texto'], y=classificacao_lula["soma"], text=classificacao_lula["soma"]),
    go.Bar(name='Bolsonaro', x=classificacao_bolsonaro['classificacao_texto'], y=classificacao_bolsonaro["soma"], text=classificacao_bolsonaro["soma"]),
])
# Change the bar mode
fig.update_layout(barmode='group', title = 'Comparação de Quantidade de Classificações entre Lula e Bolsonaro')
fig.show()

Lembrando nem todos os tweets mencionam os presidentes diretamente e tweets podem mencionar os dois candidatos, na época que foram baixados os dados. Então podemos verificar também que os dois candidatos possuem a quantidade de dados equilibradas no total.

#### Tratamento

Aqui fazemos os tratamentos dos dados removendo as stopwords.

In [11]:
tweets['full_text'] = tweets['full_text'].apply(ajustandoDados.remove_stopwords)
tweets['full_text'][1]

['jair', 'desespero']

Aqui normalizamos as palavras do dataset utilizando lemmatize, aqui estamos encontrando o lema da palavra de mandeira que é considerado o contexto da frase

[Conceito de lemmatize](https://www.guru99.com/stemming-lemmatization-python-nltk.html)

[Conceito de lemma ou lema](https://simple.wikipedia.org/wiki/Lemma_(linguistics))

In [12]:
tweets['full_text'] = tweets['full_text'].apply(ajustandoDados.lemmatize_word)
tweets['full_text'][1]

'jair desespero'

#### Criando o modelo

Primeiro iremos selecionar os dados que serão previstos e o que serão utilizados para prever.

Após isso iremos utilizar o [CountVectorizer](https://www.geeksforgeeks.org/using-countvectorizer-to-extracting-features-from-text/) para transformar o texto em um vetor baseado na frequência de cada palavra que ocorre no texto, nosso caso no dataset.

Após isso imprimos o formato de x e y.

In [30]:
from sklearn.feature_extraction.text import CountVectorizer
#Transformamos os tweets em array.
x = np.array(tweets.iloc[:,0].values)
#Transformamos as classificações em array.
y = np.array(tweets['classificacao'].values)
#Aqui no COuntVectorizer definifimos para ignorar termos com uma frequência menor que 0.3 e maior que 0.7 nos documentos.
#Após isso definimos as a matriz de características a partir de 200 palavras mais frequentes nos documentos.
cv = CountVectorizer(min_df=0.2, max_df=0.7, max_features=200)
#
x = cv.fit_transform(tweets['full_text']).toarray()
print("X.shape = ",x.shape)
print("y.shape = ",y.shape)

X.shape =  (413, 3)
y.shape =  (413,)


Aqui iremos separar os dados entre dados de treino e dados de teste.

In [31]:
from sklearn.model_selection import train_test_split
#Aqui divimos o dataset em teste e treino, 80% do dataset será para treino do modelo e 20% para teste.
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size = 0.10, random_state = 0, shuffle = True)
print(len(x_train))
print(len(x_test))

371
42


Aqui definimos vários modelos para prevermos qual obtem o melhor resultado, isso poderemos ver na tabela que é criada com o resultado com o score de cada modelo.

In [32]:
def run_model(model_name, x_train, y_train):
    '''
      Aqui definimos uma função que irá rodar os modelos de Decision Tree e Random Forests.
    '''
    mdl=''
    if model_name == 'Random Forest':
      #Definimos que a floresta terá 50 árvores.
      mdl = RandomForestClassifier(n_estimators=50)
    elif model_name == 'Decision Tree Classifier':
      mdl = DecisionTreeClassifier()

    #Fazemos com que sejam construidas as florestas, no caso do modelo de Random Forests,
    #ou que sejam construída a árvore, no caso da Decision Tree.
    mdl.fit(x_train, y_train)
    #Aqui testamos os modelo treinado nos dados de teste
    y_pred = mdl.predict(x_test)

    # Performance metrics
    accuracy = round(accuracy_score(y_test, y_pred) * 100, 2)

    # Get precision, recall, f1 scores
    precision, recall, f1score, support = score(y_test, y_pred, average='micro')
    
    # Add performance parameters to list
    perform_list.append(dict([
      ('Model', model_name),
      ('Test Accuracy', round(accuracy, 2)),
      ('Precision', round(precision, 2)),
      ('Recall', round(recall, 2)),
      ('F1', round(f1score, 2))
    ]))


In [33]:
#Criando a lista de performance 
perform_list = []

#Rodando o modelo e verificando 
run_model('Random Forest', x_train, y_train)
run_model('Decision Tree Classifier', x_train, y_train)

result = pd.DataFrame(perform_list)
display(result)

Model  Test Accuracy  Precision  Recall    F1
0             Random Forest          52.38       0.52    0.52  0.52
1  Decision Tree Classifier          50.00       0.50    0.50  0.50

#### Testando o Modelo

Aqui criamos um dataframe com frases novas para verificarmos como o modelo se comporta com frases novas.

In [34]:
teste = [['Gosto muito do presidente Lula'],
         ['Gosto muito do presidente Bolsonaro'], 
         ['Lula foi um ladrão e merece ir para a cadeia!!!'],
         ['Bolsonaro foi um ladrão e merece ir para a cadeia!!!'],
         ['Bolsonaro foi um dos piores presidentes do brasil, robou e fez o que queria para se manter no poder'],
         ['Lula foi um dos piores presidentes do brasil, robou e fez o que queria para se manter no poder'], 
         ['jair bolsonaro foi muito bom para o povo brasileiro, deu oportunidades, emprego!!!!'],
         ['lula foi muito bom para o povo brasileiro, deu oportunidades, emprego!!!!']]
dfTeste = pd.DataFrame(teste, columns=['frase_teste'])
ajustandoDados.remove_misc1(dfTeste, 'frase_teste')
dfTeste['frase_teste'] = dfTeste['frase_teste'].apply(ajustandoDados.remove_stopwords)
dfTeste['frase_teste'] = dfTeste['frase_teste'].apply(ajustandoDados.lemmatize_word)
dfTeste

frase_teste
0                              gosto presidente lula
1                         gosto presidente bolsonaro
2                 lula ladrao merece ir cadeia ! ! !
3            bolsonaro ladrao merece ir cadeia ! ! !
4  bolsonaro piores presidentes brasil , robou fe...
5  lula piores presidentes brasil , robou fez que...
6  jair bolsonaro bom povo brasileiro , deu oport...
7  lula bom povo brasileiro , deu oportunidades ,...

Aqui pegamos os mesmos CountVectorizer, as mesmas keywords arguments para os modelos e as mesma categorias alvo.

In [35]:
y_teste = cv.transform(dfTeste['frase_teste'])
mdl_RF = RandomForestClassifier(n_estimators=50).fit(x_train, y_train)
mdl_DT = DecisionTreeClassifier().fit(x_train, y_train)

y_pred_RF = mdl_RF.predict(y_teste)
y_pred_DT = mdl_DT.predict(y_teste)

resultado_RF = categoria_alvo[y_pred_RF]
resultado_DT = categoria_alvo[y_pred_DT]

resultados = pd.DataFrame()
resultados['frases'] = dfTeste['frase_teste']
resultados['RF'] = resultado_RF
resultados['DT'] = resultado_DT


display(resultados)

frases        RF        DT
0                              gosto presidente lula  negativo  negativo
1                         gosto presidente bolsonaro  positivo  positivo
2                 lula ladrao merece ir cadeia ! ! !  negativo  negativo
3            bolsonaro ladrao merece ir cadeia ! ! !  positivo  positivo
4  bolsonaro piores presidentes brasil , robou fe...  positivo  positivo
5  lula piores presidentes brasil , robou fez que...  negativo  negativo
6  jair bolsonaro bom povo brasileiro , deu oport...  positivo  positivo
7  lula bom povo brasileiro , deu oportunidades ,...  negativo  negativo

No resultado acima verificamos que o modelo está enviesado para que quando o Lula é mencionado a classificação é negativa ou neutra e quando Bolsonaro é mencionado verificamos que a classificação tende a ser possitiva.

In [36]:
fn = cv.get_feature_names_out(y_teste)
print(len(fn))

3


In [38]:
fig_tree = plt.figure(figsize=(100,120))
_ = tree.plot_tree(mdl_DT,
                   feature_names=fn,
                   class_names=resultados.DT,
                   filled=True)

plt.show()
fig_tree.savefig("decistion_tree.png")

In [28]:
estimator = mdl_RF.estimators_[0]
fig_forest = plt.figure(figsize=(100,120))
_ = tree.plot_tree(estimator,
                   feature_names=fn,
                   class_names=resultados.RF,
                   filled=True)

plt.show()
fig_forest.savefig("random_forest.png")

In [302]:
filename = 'C:/Users/rafae/OneDrive/Documents/GitHub/Tweet_Classifier/Final/cod/modelo/classificadores/RandomForestClassifier_tweets.sav'
model = RandomForestClassifier(n_estimators=50).fit(x_train, y_train)
joblib.dump(model, filename)

filename = 'C:/Users/rafae/OneDrive/Documents/GitHub/Tweet_Classifier/Final/cod/modelo/classificadores/DecisionTreeClassifier_tweets.sav'
model = DecisionTreeClassifier().fit(x_train, y_train)
joblib.dump(model, filename)

# salvando o vetorizador:
filename = 'C:/Users/rafae/OneDrive/Documents/GitHub/Tweet_Classifier/Final/cod/modelo/classificadores/vectorizer_tweets.sav'
joblib.dump(cv, filename)

filename = 'C:/Users/rafae/OneDrive/Documents/GitHub/Tweet_Classifier/Final/cod/modelo/classificadores/categoria_alvo_tweets.sav'
joblib.dump(categoria_alvo, filename)

['C:/Users/rafae/OneDrive/Documents/GitHub/HCAI/Final/cod/modelo/classificadores/categoria_alvo_tweets.sav']